In [1]:
import os
import re
import json
from loguru import logger
from tqdm import tqdm
from vllm import LLM, SamplingParams

MODEL_NAME = 'Qwen/Qwen2-7B-Instruct'
#llm = LLM(model=MODEL_NAME, dtype='float16')

sampling_params = SamplingParams(
    max_tokens=1024
)
import openai
client = openai.Client(
    base_url="http://127.0.0.1:30000/v1", api_key="EMPTY")


In [2]:
def get_prompt(problem, question, options):
    options = '\n'.join(f"{'ABCDEFG'[i]}. {o}" for i, o in enumerate(options))

    prompt = f"""你是一位逻辑推理专家。请分析并解答以下单选题,遵循闭世界假设(未明确陈述的事实均为假)。
                ### 题目:
                {problem}
                
                ### 问题:
                {question}
                {options}
                
                请按以下步骤进行:
                1. 列出关键信息和事实
                2. 分析每个选项的逻辑
                3. 解释你的推理过程
                4. 得出结论
                
                简短且用清晰的结构呈现你的分析。如果是数学题，直接给出答案。字数限定在150字以内且必须包括答案。
                
                最后,以此格式给出答案:
                答案是：#选项字母#
                
                ### 例如：
                # 题目
                下面是一道关于计算阶乘的选择题：已知如下规则：1. 数字 0 的阶乘是 1。2. 数字 N 的阶乘等于 N 乘以 N-1 的阶乘。请根据此规则回答以下问题：
                # 问题
                选择题 1：7 的阶乘是多少？
                A. 720
                B. 40320
                C. 5040
                D. 362880
                
                # 答案
                答案是：C            
            """
    return prompt


In [3]:
# 这里使用extract抽取模获得抽取的结果

def extract(input_text):
    ans_pattern = re.compile(r"答案是：(.)", re.S)

    problems = ans_pattern.findall(input_text)
    if (problems == ''):
        return 'A'
    return problems[0]

In [4]:
def process_datas(datas):
    results = []

    future_data = {}
    lens = 0
    for data in tqdm(datas, desc="Submitting tasks", total=len(datas)):

        problem = data['problem']
        messages = []
        for id, question in enumerate(data['questions']):
            prompt = get_prompt(problem,
                                question['question'],
                                question['options'],
                                )
            messages.append(prompt)
        
        #response = llm.generate(messages, sampling_params)
        response = client.completions.create(
                            model="default",
                            prompt=messages,
                            temperature=0,
                            max_tokens=512,
                        )
        print(messages)
        print(response)
        for id, future in enumerate(response):
            future_data[response.choices[0].text] = (data, id)
            lens += 1
            
    for future in tqdm(future_data, total=lens, desc="Processing tasks"):
        data = future_data[future][0]
        problem_id = future_data[future][1]
        try:
            res = future
            extract_response = extract(res)
            print(extract_response)
            data['questions'][problem_id]['answer'] = extract_response
            results.append(data)
        except Exception as e:
            logger.error(f"Failed to process text: {data}. Error: {e}")

    return results

In [5]:
def main(ifn, ofn):
    if os.path.exists(ofn):
        pass
    data = []
    # 按行读取数据
    with open(ifn) as reader:
        for line in reader:
            sample = json.loads(line)
            data.append(sample)
    datas = data
    return_list = process_datas(datas)
    print(len(return_list))
    print("All tasks finished!")
    return return_list

In [6]:
def evaluate(ofn):
    data = []
    with open(ofn) as reader:
        for line in reader:
            sample = json.loads(line)
            data.append(sample)

    pse = 0
    cnt = 0
    tot = 0
    for task in data:
        for question in task['questions']:

            if MODEL_NAME in question:
                tot += 1
                cnt += question[MODEL_NAME] == question['answer']
            else:
                pse += 1

    print(cnt, tot, cnt / tot, pse)

In [7]:
if __name__ == '__main__':
    return_list = main('round1_test_data.jsonl', 'upload.jsonl')


Submitting tasks:   0%|          | 1/500 [00:04<35:37,  4.28s/it]

['你是一位逻辑推理专家。请分析并解答以下单选题,遵循闭世界假设(未明确陈述的事实均为假)。\n                ### 题目:\n                有一群人和一些食物类型。下列是关于这些个体和食物的已知信息：\n\n1. 鸡肉是一种食物。\n2. 苹果是一种食物。\n3. 如果X吃了Y，且X活着，则Y是一种食物。\n4. Bill存活。\n5. Bill吃了花生。\n6. John吃所有食物。\n7. Sue吃所有Bill吃的食物。\n8. John喜欢所有食物。\n\n根据以上信息，回答以下选择题：\n                \n                ### 问题:\n                选择题 1：\n谁喜欢吃花生？\n                A. Bill\nB. Sue\nC. John\nD. None of the above\n                \n                请按以下步骤进行:\n                1. 列出关键信息和事实\n                2. 分析每个选项的逻辑\n                3. 解释你的推理过程\n                4. 得出结论\n                \n                简短且用清晰的结构呈现你的分析。如果是数学题，直接给出答案。字数限定在150字以内且必须包括答案。\n                \n                最后,以此格式给出答案:\n                答案是：#选项字母#\n                \n                ### 例如：\n                # 题目\n                下面是一道关于计算阶乘的选择题：已知如下规则：1. 数字 0 的阶乘是 1。2. 数字 N 的阶乘等于 N 乘以 N-1 的阶乘。请根据此规则回答以下问题：\n                # 问题\n                选择题 1：7 的阶乘是多少？\n                A. 720\n                B. 40320\n    

Submitting tasks:   0%|          | 2/500 [00:10<44:30,  5.36s/it]

['你是一位逻辑推理专家。请分析并解答以下单选题,遵循闭世界假设(未明确陈述的事实均为假)。\n                ### 题目:\n                设有两个列表操作，第一个列表中包含若干元素，并且可以将第二个列表的元素追加到第一个列表的末尾形成一个新的列表。根据这个操作，请回答以下问题：\n                \n                ### 问题:\n                选择题 1：\n当第一个列表是[a, b, c]，第二个列表是[d, e]时，新的列表是什么？\n                A. [a, b, c, d]\nB. [a, d, e, b, c]\nC. [a, b, c, d, e]\nD. [d, e, a, b, c]\n                \n                请按以下步骤进行:\n                1. 列出关键信息和事实\n                2. 分析每个选项的逻辑\n                3. 解释你的推理过程\n                4. 得出结论\n                \n                简短且用清晰的结构呈现你的分析。如果是数学题，直接给出答案。字数限定在150字以内且必须包括答案。\n                \n                最后,以此格式给出答案:\n                答案是：#选项字母#\n                \n                ### 例如：\n                # 题目\n                下面是一道关于计算阶乘的选择题：已知如下规则：1. 数字 0 的阶乘是 1。2. 数字 N 的阶乘等于 N 乘以 N-1 的阶乘。请根据此规则回答以下问题：\n                # 问题\n                选择题 1：7 的阶乘是多少？\n                A. 720\n                B. 40320\n                C. 5040\n                D. 362880\n

Submitting tasks:   1%|          | 3/500 [00:12<30:27,  3.68s/it]

...

['你是一位逻辑推理专家。请分析并解答以下单选题,遵循闭世界假设(未明确陈述的事实均为假)。\n                ### 题目:\n                ```自然语言测试题：\n\n考虑一个函数，它能够生成一个从1开始到给定数字N的列表。若函数以0作为输入，返回的列表应为空。基于此描述，请选择以下选项中正确的结果：\n                \n                ### 问题:\n                选择题 1：\n如果N等于0，该函数返回什么？\n                A. [0]\nB. [1]\nC. []\nD. [1, 2, 3,..., N]\n                \n                请按以下步骤进行:\n                1. 列出关键信息和事实\n                2. 分析每个选项的逻辑\n                3. 解释你的推理过程\n                4. 得出结论\n                \n                简短且用清晰的结构呈现你的分析。如果是数学题，直接给出答案。字数限定在150字以内且必须包括答案。\n                \n                最后,以此格式给出答案:\n                答案是：#选项字母#\n                \n                ### 例如：\n                # 题目\n                下面是一道关于计算阶乘的选择题：已知如下规则：1. 数字 0 的阶乘是 1。2. 数字 N 的阶乘等于 N 乘以 N-1 的阶乘。请根据此规则回答以下问题：\n                # 问题\n                选择题 1：7 的阶乘是多少？\n                A. 720\n                B. 40320\n                C. 5040\n                D. 362880\n                \n                # 答案\n     

Submitting tasks: 100%|██████████| 500/500 [47:11<00:00,  5.66s/it]


['你是一位逻辑推理专家。请分析并解答以下单选题,遵循闭世界假设(未明确陈述的事实均为假)。\n                ### 题目:\n                以下为自然语言描述的单项选择测试题，基于给定的 Prolog 代码及其问题和答案：\n\n有以下四个函数描述：\n\n1. **Square 函数**：输入一个列表，输出一个新列表，包含原列表中每个元素的平方。\n\n2. **Sum 函数**：输入一个列表，输出该列表的所有元素的和。\n\n3. **Sumn 函数**：输入一个非负整数，输出从 1 到该整数的所有自然数的和。\n\n4. **Dup 函数**：输入一个列表，输出一个新列表，每个元素在其中出现两次。\n\n根据上述描述，回答以下选择题：\n                \n                ### 问题:\n                选择题 1：\n对 "sumn" 函数的调用 sumn(3, Y) 会得到什么结果？\n                A. 3\nB. 6\nC. 9\nD. 12\n                \n                请按以下步骤进行:\n                1. 列出关键信息和事实\n                2. 分析每个选项的逻辑\n                3. 解释你的推理过程\n                4. 得出结论\n                \n                简短且用清晰的结构呈现你的分析。如果是数学题，直接给出答案。字数限定在150字以内且必须包括答案。\n                \n                最后,以此格式给出答案:\n                答案是：#选项字母#\n                \n                ### 例如：\n                # 题目\n                下面是一道关于计算阶乘的选择题：已知如下规则：1. 数字 0 的阶乘是 1。2. 数字 N 的阶乘等于 N 乘以 N-1 的阶乘。请根据此规则回答以下问题：\n                # 问题\n        

Processing tasks:   0%|          | 0/3500 [00:00<?, ?it/s]2024-07-29 13:07:06.893 | ERROR    | __main__:process_datas:40 - Failed to process text: {'problem': '有一群人和一些食物类型。下列是关于这些个体和食物的已知信息：\n\n1. 鸡肉是一种食物。\n2. 苹果是一种食物。\n3. 如果X吃了Y，且X活着，则Y是一种食物。\n4. Bill存活。\n5. Bill吃了花生。\n6. John吃所有食物。\n7. Sue吃所有Bill吃的食物。\n8. John喜欢所有食物。\n\n根据以上信息，回答以下选择题：', 'questions': [{'question': '选择题 1：\n谁喜欢吃花生？', 'options': ['Bill', 'Sue', 'John', 'None of the above']}], 'id': 'round1_test_data_000'}. Error: list index out of range
2024-07-29 13:07:06.893 | ERROR    | __main__:process_datas:40 - Failed to process text: {'problem': '设有两个列表操作，第一个列表中包含若干元素，并且可以将第二个列表的元素追加到第一个列表的末尾形成一个新的列表。根据这个操作，请回答以下问题：', 'questions': [{'question': '选择题 1：\n当第一个列表是[a, b, c]，第二个列表是[d, e]时，新的列表是什么？', 'options': ['[a, b, c, d]', '[a, d, e, b, c]', '[a, b, c, d, e]', '[d, e, a, b, c]']}, {'question': '选择题 2：\n如果新列表是[a, b, c, d, e]，而第二个列表是[d, e]，那么第一个列表是什么？', 'options': ['[a]', '[a, b]', '[a, b, c]', '[b, c]']}, {'question': '选择题 3：\n当第一

A
A
D
A
C
A
#
C
A
D
A
C
*
B
C
C
B
C
A
C
B
B
A
B
A
C
C
D
C


A
B
C
C
A
B
A
无
B
D
A
B
D
B
A
C
B
A
D
B
#
D
C
A
A
C
D
C
D
B
A
C
C
A
A
B
C
A
C
D
C
B
B
无
C
C
D
C
A
C
C
C
A
D
B
B
D
A
C
A
D
C
B
B
D
C
D
B
D
A
C
B
C
A
A
B
C
B
B
C
A
A
B
B
C
C
C
D
无
A
B
C
*
C
B
C
A
C
C


B
A
A
A
D
A
#
A
B
B
A
C
B
C
D
A
B
A
C
B
C
D
C
A
A
A
C
B
D
B
B
D
D
C
B


C
A
D
D
B
C
A
#
B
C
A
B
C
C
A
D
A
B
无
A
B
D
A
B
B
A
C


A
C
C
A


B
B
*
B
C
C
C
C


C
A
B
E
A
B
A


#
B


B
A
C
无
A
B
B
B
C
A
A
A
D
C
B
D
A
B
D
B
A
C
D
B
B
A
B
A
A
D
B
C
B
A
C
C
A
C


D
B
C
C
B
C
B
A
A
B
B
B
A
C
C
B
A
C
B
A
#
A
A
A
A
C
D
C


A
C
B
A
B
D
B
B
B
B
A
B
B
C


B
A
C
D
C
C
C
#
B
D
A
C


A
A
B
B
A
D
C
D
A
A
A
C
A
B
C
C
B
D
B
B
B
C
C
A
B
C
C
B
B
D
B
B
A
B
B
C
D
C
C
C
B
B
C
A
C
B
B
E
A
C
A
A
C
C
C
B
A
B
C
C
A
A
无
B
无
B
C
A
B
C
C
C
C
C
A
C
A
C
C
B
C
B
A
B
B
C
C
C
B
D
C
C
A
A
D
B
B
C
C
A
A
A
A
B
B
D
无
C
B
A
C
B
C
A
A
A
A




B
D
B
C
B
B
C
C
C
C
A
B
A
A
C
B
B
B
A
C
D
B
C
C
B
C
A
B
C
C
D
D
B
C
C
C
C
B
C
D
C
C
A
A
C
C
A
B
A
A
A
B
C
B
0
All tasks finished!


In [8]:
def has_complete_answer(questions):
    # 这里假设完整答案的判断逻辑是：每个question都有一个'answer'键
    for question in questions:
        if 'answer' not in question:
            return False
    return True


def filter_problems(data):
    result = []
    problem_set = set()

    for item in data:
        # print('处理的item' ,item)
        problem = item['problem']
        if problem in problem_set:
            # 找到已存在的字典
            for existing_item in result:
                if existing_item['problem'] == problem:
                    # 如果当前字典有完整答案，替换已存在的字典
                    if has_complete_answer(item['questions']):
                        existing_item['questions'] = item['questions']
                        existing_item['id'] = item['id']
                    break
        else:
            # 如果当前字典有完整答案，添加到结果列表
            if has_complete_answer(item['questions']):
                result.append(item)
                problem_set.add(problem)

    return result

In [9]:
return_list
return_list = filter_problems(return_list)
sorted_data = sorted(return_list, key=lambda x: int(str(x['id'])[-3:]))
print(sorted_data)

[]


In [10]:
sorted_data

[]

In [11]:
def find_missing_ids(dict_list):
    # 提取所有序号
    extracted_ids = {int(d['id'][-3:]) for d in dict_list}

    # 创建0-500的序号集合
    all_ids = set(range(500))

    # 找出缺失的序号
    missing_ids = all_ids - extracted_ids

    return sorted(missing_ids)


# 示例字典列表
dict_list = sorted_data

# 找出缺失的序号
missing_ids = find_missing_ids(dict_list)
print("缺失的序号:", missing_ids)

缺失的序号: [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 22

In [12]:
len(missing_ids)

500

In [13]:
data = []
with open('round1_test_data.jsonl') as reader:
    for id, line in enumerate(reader):
        if (id in missing_ids):
            sample = json.loads(line)
            for question in sample['questions']:
                question['answer'] = 'A'
            sorted_data.append(sample)
sorted_data = sorted(sorted_data, key=lambda x: int(str(x['id'])[-3:]))


In [14]:
with open('upload-pipeline.jsonl', 'w') as writer:
    for sample in sorted_data:
        writer.write(json.dumps(sample, ensure_ascii=False))
        writer.write('\n')

In [15]:
import openai
client = openai.Client(
    base_url="http://127.0.0.1:30000/v1", api_key="EMPTY")

# Text completion
response = client.completions.create(
	model="default",
	prompt="The capital of France is",
	temperature=0,
	max_tokens=32,
)
print(response.choices[0].text) 

 Paris. It is also the largest city in France. Paris is a major international center of art, science and fashion. The Louvre is the world's largest
